In [1]:
import pandas as pd
from sklearn.model_selection import train_test_split

import prepare
import model
df = pd.read_csv('healthcare-dataset-stroke-data.csv')

In [2]:
# prepare data using script
df = prepare.prep_data(df).drop(columns=['age_range', 'id'])
df.stroke.dtype

dtype('O')

In [3]:
# cast stroke column as int
df['stroke'] = df['stroke'].astype('int64')
# check work
df.shape

(5109, 11)

In [4]:
# check work
df.head(3)

gender   age hypertension heart_disease ever_married      work_type  \
0    Male  67.0            0             1          Yes        Private   
1  Female  61.0            0             0          Yes  Self-employed   
2    Male  80.0            0             1          Yes        Private   

  residence_type  avg_glucose_level        bmi   smoking_status  stroke  
0          Urban             228.69  36.600000  formerly smoked       1  
1          Rural             202.21  30.640331     never smoked       1  
2          Rural             105.92  32.500000     never smoked       1

In [5]:
# set list of columns to one-hot encode
col_list = ['gender','ever_married','work_type','residence_type','smoking_status']
# apply one-hot encoding using above list
df = pd.get_dummies(df, columns=col_list, drop_first=True)

In [6]:
# split using same random state as explore stage
trainvalidate, test = train_test_split(df, test_size=.2, random_state=777)
train, validate = train_test_split(trainvalidate, test_size=.25, random_state=777)
# check work
train.shape, validate.shape, test.shape

((3065, 16), (1022, 16), (1022, 16))

In [7]:
# isolate target
X_train, y_train = train.drop(columns='stroke'), train.stroke
X_validate, y_validate = validate.drop(columns='stroke'), validate.stroke
X_test, y_test = test.drop(columns='stroke'), test.stroke

In [8]:
# apply scaling using a MinMaxScaler
scaler, X_train_scaled, X_validate_scaled, X_test_scaled = model.Min_Max_Scaler(X_train, X_validate, X_test)

In [9]:
# build & fit models, append model predictions to the train and validate actuals dataframes
y_train_predictions,\
y_validate_predictions = model.classification_shotgun(X_train_scaled, y_train, X_validate_scaled, y_validate)

In [10]:
pd.set_option("display.max_rows", None, "display.max_columns", None)
y_train_predictions

in_actuals  baseline  cv_tree_maxdepth1  cv_tree_maxdepth2  \
448            0         0                  0                  0   
4128           0         0                  0                  0   
4699           0         0                  0                  0   
5035           0         0                  0                  0   
3007           0         0                  0                  0   
3212           0         0                  0                  0   
2154           0         0                  0                  0   
1695           0         0                  0                  0   
4451           0         0                  0                  0   
2380           0         0                  0                  0   
2538           0         0                  0                  0   
3809           0         0                  0                  0   
1459           0         0                  0                  0   
1068           0         0                  0                  0   
3290           0         0                  0                  0   
4152           0         0                  0                  0   
2819           0         0                  0                  0   
166            1         0                  0                  0   
2325           0         0                  0                  0   
4338           0         0                  0                  0   
739            0         0                  0                  0   
3688           0         0                  0                  0   
3533           0         0                  0                  0   
3480           0         0                  0                  0   
2474           0         0                  0                  0   
2500           0         0                  0                  0   
293            0         0                  0                  0   
860            0         0                  0                  0   
184            1         0                  0                  0   
1770           0         0                  0                  0   
531            0         0                  0                  0   
150            1         0                  0                  0   
4592           0         0                  0                  0   
2606           0         0                  0                  0   
4885           0         0                  0                  0   
4995           0         0                  0                  0   
1874           0         0                  0                  0   
4395           0         0                  0                  0   
3415           0         0                  0                  0   
26             1         0                  0                  0   
491            0         0                  0                  0   
3585           0         0                  0                  0   
1750           0         0                  0                  0   
1810           0         0                  0                  0   
187            1         0                  0                  0   
2060           0         0                  0                  0   
4549           0         0                  0                  0   
2923           0         0                  0                  0   
1477           0         0                  0                  0   
4691           0         0                  0                  0   
3333           0         0                  0                  0   
3924           0         0                  0                  0   
3073           0         0                  0                  0   
2996           0         0                  0                  0   
4878           0         0                  0                  0   
925            0         0                  0                  0   
3899           0         0                  0                  0   
3285           0         0                  0                 

In [11]:
# calculate accuracy and recall for in- and out-sample predictions
running_df = model.print_classification_results(y_train_predictions, y_validate_predictions)

In [12]:
# display accuracies and recalls for each model, sorting for best out-sample recall
running_df.sort_values(by='OutSample_Recall', ascending=False)

Model  InSample_Accuracy  OutSample_Accuracy  \
13     nb_vsmooth1e-08           0.377162            0.383562   
12     nb_vsmooth1e-09           0.351387            0.354207   
14     nb_vsmooth1e-07           0.424144            0.428571   
15     nb_vsmooth1e-06           0.497879            0.510763   
16     nb_vsmooth1e-05           0.578467            0.588063   
17    nb_vsmooth0.0001           0.688091            0.695695   
18     nb_vsmooth0.001           0.769984            0.785714   
19      nb_vsmooth0.01           0.825122            0.839530   
5   cv_tree_maxdepth10           0.980098            0.949119   
22              knn_n3           0.956281            0.951076   
25             knn_n25           0.951060            0.956947   
24             knn_n10           0.951387            0.956947   
23              knn_n5           0.953670            0.954990   
21       nb_vsmooth100           0.950734            0.956947   
20        nb_vsmooth10           0.950734            0.956947   
0             baseline           0.950734            0.956947   
1    cv_tree_maxdepth1           0.950734            0.956947   
11               logit           0.951387            0.956947   
10          rf_depth10           0.970310            0.955969   
9            rf_depth5           0.951387            0.956947   
8            rf_depth3           0.950734            0.956947   
7            rf_depth2           0.950734            0.956947   
6            rf_depth1           0.950734            0.956947   
4    cv_tree_maxdepth5           0.954323            0.954990   
3    cv_tree_maxdepth3           0.950734            0.956947   
2    cv_tree_maxdepth2           0.950734            0.956947   
26             knn_n75           0.950734            0.956947   

    InSample_Recall  OutSample_Recall  
13         0.980132          1.000000  
12         0.980132          1.000000  
14         0.953642          0.931818  
15         0.920530          0.909091  
16         0.894040          0.886364  
17         0.807947          0.795455  
18         0.695364          0.659091  
19         0.569536          0.545455  
5          0.609272          0.136364  
22         0.172185          0.022727  
25         0.006623          0.000000  
24         0.019868          0.000000  
23         0.086093          0.000000  
21         0.000000          0.000000  
20         0.000000          0.000000  
0          0.000000          0.000000  
1          0.000000          0.000000  
11         0.013245          0.000000  
10         0.397351          0.000000  
9          0.013245          0.000000  
8          0.000000          0.000000  
7          0.000000          0.000000  
6          0.000000          0.000000  
4          0.119205          0.000000  
3          0.000000          0.000000  
2          0.000000          0.000000  
26         0.000000          0.000000